<h1> DSC 170: Lecture 6. Geoenrichment, and navigating different types of vector representation in  ArcGIS API for Python</h1>

This lecture will cover:
* Geonrichment  
  - a key approach to engineering features for analysis
  - understand what information available, and how to retrieve it
  - adding features to existing named areas, and to constructed areas
  - understand data accuracy issues
* Navigating different type of feature data in ArcGIS  
  - different types of feature representations, with different conversion and analysis APIs
  - what you can do with feature data


## How do we get statistical data for mapping and spatial analysis (e.g., from the Census)?

Without a centralized catalog in AGOL, we have to explore multiple databases

For example, to retrieve data from the Census Bureau, we can use a Python wrapper over Census data API

In [1]:
# Getting Census data
import cenpy # a python wrapper over Census data API

/Users/amolkale/Documents/DSE/DSE260-Capstone-Project/capstone/venv3.9/lib/python3.9/site-packages/fuzzywuzzy/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
!python --version

Python 3.9.16


**The American Community Survey (ACS)** is a survey conducted by the U.S. Census Bureau to collect data on a wide range of topics, including demographic, economic, and social characteristics of the U.S. population. It is conducted every year, with additional estimates produced every 5 years (3-year summaries have been discontinued). The ACS is the largest household survey in the United States, and it covers the entire U.S. population, including both rural and urban areas. See https://www.census.gov/programs-surveys/acs/guidance/estimates.html

In [3]:
# Can include a year as parameter, or leave blank for the latest

acs = cenpy.products.ACS() 

In [4]:
acs

Connection to American Community Survey: 5-Year Estimates: Detailed Tables 5-Year(ID: https://api.census.gov/data/id/ACSDT5Y2019)
With MapServer: Census ACS 2019 WMS

In [5]:
# retrieving spatial data for San Diego:
sandiego = acs.from_county(county="San Diego, CA", level='tract',return_geometry=True)

/Users/amolkale/Documents/DSE/DSE260-Capstone-Project/capstone/venv3.9/lib/python3.9/site-packages/cenpy/products.py:762: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  return self._from_name(county, variables, level, "Counties", **kwargs)


In [6]:
sandiego.head()

GEOID                                           geometry  \
0  06073010012  POLYGON ((-13031330.990 3837056.990, -13031329...   
1  06073010009  POLYGON ((-13032295.570 3834831.280, -13032295...   
2  06073018609  POLYGON ((-13060305.560 3928579.880, -13060303...   
3  06073017813  POLYGON ((-13062844.310 3914484.240, -13062763...   
4  06073017701  POLYGON ((-13059537.230 3907015.040, -13059431...   

                                                NAME state county   tract  
0  Census Tract 100.12, San Diego County, California    06    073  010012  
1  Census Tract 100.09, San Diego County, California    06    073  010009  
2  Census Tract 186.09, San Diego County, California    06    073  018609  
3  Census Tract 178.13, San Diego County, California    06    073  017813  
4  Census Tract 177.01, San Diego County, California    06    073  017701

In [7]:
sandiego.explore()

In [8]:
vars_to_download = {
    "B25077_001E": "median_house_value",  # Median house value
    "B02001_002E": "total_pop_white",     # Total white population
    "B01003_001E": "total_pop",           # Total population
    "B25003_003E": "total_rented",        # Total rented occupied
    "B25001_001E": "total_housing_units", # Total housing units
    "B09019_006E": "hh_female",           # Female households
    "B09019_001E": "hh_total",            # Total households
    "B15003_002E": "total_bachelor",      # Total w/ Bachelor degree
    "B25018_001E": "median_no_rooms",     # Median number of rooms
    "B19083_001E": "income_gini",         # Gini index of income inequality
    "B01002_001E": "median_age",          # Median age
    "B08303_001E": "tt_work",              # Aggregate travel time to work
    "B19013_001E": "median_hh_income"     # Median household income
}
vars_to_download_l = list(vars_to_download.keys())

In [9]:
%%time
sandiego_subset = acs.from_msa("San Diego, CA",
                  level="tract",
                  variables=vars_to_download_l
                 )

CPU times: user 1.59 s, sys: 75.7 ms, total: 1.66 s
Wall time: 14 s


/Users/amolkale/Documents/DSE/DSE260-Capstone-Project/capstone/venv3.9/lib/python3.9/site-packages/cenpy/products.py:748: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  return self._from_name(


In [10]:
sandiego_subset

# !! You may need this in your final projects !!

GEOID                                           geometry  \
0    06073010012  POLYGON ((-13031330.990 3837056.990, -13031329...   
1    06073010009  POLYGON ((-13032295.570 3834831.280, -13032295...   
2    06073018609  POLYGON ((-13060305.560 3928579.880, -13060303...   
3    06073017813  POLYGON ((-13062844.310 3914484.240, -13062763...   
4    06073017701  POLYGON ((-13059537.230 3907015.040, -13059431...   
..           ...                                                ...   
623  06073015501  POLYGON ((-13012544.490 3870123.230, -13012524...   
624  06073015502  POLYGON ((-13008615.020 3871069.090, -13008603...   
625  06073021206  POLYGON ((-13002757.840 3875229.320, -13002735...   
626  06073020904  POLYGON ((-12995534.090 3893829.790, -12995531...   
627  06073020902  POLYGON ((-13001033.500 3883654.180, -13001032...   

     B01002_001E  B01003_001E  B02001_002E  B08303_001E  B09019_001E  \
0           30.1       5199.0       4598.0       2116.0       5199.0   
1           30.0       6978.0       5957.0       3034.0       6978.0   
2           35.0       6437.0       4521.0       3255.0       6437.0   
3           49.6       4018.0       3516.0       1366.0       4018.0   
4           38.4       5141.0       4546.0       2267.0       5141.0   
..           ...          ...          ...          ...          ...   
623         43.6       5180.0       4376.0       2253.0       5180.0   
624         42.7       2889.0       2580.0       1262.0       2889.0   
625         41.2       3274.0       3050.0       1421.0       3274.0   
626         57.2       2223.0       1906.0        751.0       2223.0   
627         49.1       2235.0       1907.0        834.0       2235.0   

     B09019_006E  B15003_002E  B19013_001E  B19083_001E  B25001_001E  \
0          436.0        141.0      47750.0       0.3977       1361.0   
1          886.0        103.0      46788.0       0.4292       1723.0   
2          824.0        164.0      74958.0       0.3516       1900.0   
3          635.0         29.0     109189.0       0.4581       2228.0   
4          917.0         31.0      91667.0       0.5103       2731.0   
..           ...          ...          ...          ...          ...   
623        802.0         51.0      84013.0       0.3793       1916.0   
624        460.0         12.0     102708.0       0.3829       1023.0   
625        582.0          0.0     119441.0       0.3686       1147.0   
626        517.0          0.0      58558.0       0.4131       1777.0   
627        357.0          2.0      92908.0       0.3669       1169.0   

     B25003_003E  B25018_001E  B25077_001E  \
0          966.0          3.9     320100.0   
1         1194.0          4.3     447700.0   
2          655.0          5.2     337000.0   
3          447.0          5.9     891500.0   
4         1116.0          4.2    1148200.0   
..           ...          ...          ...   
623        300.0          5.9     441700.0   
624        135.0          6.4     580900.0   
625        239.0          5.6     586500.0   
626        274.0          4.5     383900.0   
627        156.0          5.0     458700.0   

                                                  NAME state county   tract  
0    Census Tract 100.12, San Diego County, California    06    073  010012  
1    Census Tract 100.09, San Diego County, California    06    073  010009  
2    Census Tract 186.09, San Diego County, California    06    073  018609  
3    Census Tract 178.13, San Diego County, California    06    073  017813  
4    Census Tract 177.01, San Diego County, California    06    073  017701  
..                                                 ...   ...    ...     ...  
623  Census Tract 155.01, San Diego County, California    06    073  015501  
624  Census Tract 155.02, San Diego County, California    06    073  015502  
625  Census Tract 212.06, San Diego County, California    06    073  021206  
626  Census Tract 209.04, San Diego County, California    06    073  020904  
627  Census Tract

In [11]:
# how to figure out which variables to retrive?
import censusdata

# this will find all variables where "household" is mentioned
#censusdata.search('acs5', 2019, 'label', '[household,age]') 

In [12]:
# such search is not always convenient...

## GeoEnrichment

This is a key capability you can use in your data science projects. It helps you to get facts about a specific area. The area can be defined by administrative boundaries, or be a result of gemoetric operations such as distance buffer or drive time from a location. Available facts are stored in multiple datasets and reflect population, income, housing, consumer behavior, and the natural environment. Much of the remainder of this notebook is based on https://developers.arcgis.com/python/guide/part1-introduction-to-geoenrichment/ and subsequent documentation sections.

The main method is **enrich()**: it retrieves info for the specified area.
The arcgis.geoenrichment module can help you create geometries to which enrich() can be later applied.

**Examples:** 
    - A wildfire analyst generates a map of the dynamics and extent of forect fires: you need to quickly determine who lives there and what their mobility charatceristics are. 
    - A company is looking for a location of a new store: you need to determine who lives in the vicinity and what they typically buy.

In [13]:
#necessary for python 3.10 since Iterable in collections was depricated in 3.9
#source https://stackoverflow.com/questions/72032032/importerror-cannot-import-name-iterable-from-collections-in-python
# import collections.abc
# #hyper needs the four following aliases to be done manually.
# collections.Iterable = collections.abc.Iterable
# collections.Mapping = collections.abc.Mapping
# collections.MutableSet = collections.abc.MutableSet
# collections.MutableMapping = collections.abc.MutableMapping
# #Now import hyper
# import hyper

In [15]:
import arcgis
from arcgis.gis import GIS
from arcgis import geometry
from arcgis.features import GeoAccessor, GeoSeriesAccessor
from arcgis.geoenrichment import *
import pandas as pd

#gis = GIS(username='izaslavsky_ucsd')  # this will ask for password. 
print("Enter the Client ID/APP ID generated from Arc GIS:")
app_id = input()
gis = GIS("https://ucsdonline.maps.arcgis.com/home", client_id=app_id)
arcgis.__version__

Enter the Client ID/APP ID generated from Arc GIS:
Elm5V3upnnV17Q3r
Please sign in to your GIS and paste the code that is obtained below.
If a web browser does not automatically open, please navigate to the URL below yourself instead.
Opening web browser to navigate to: https://ucsdonline.maps.arcgis.com/sharing/rest//oauth2/authorize?response_type=code&client_id=Elm5V3upnnV17Q3r&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&state=Fkf5szeSIYd4xevEUvUQmMCLCOc6Ip
Enter code obtained on signing in using SAML: ········


/Users/amolkale/Documents/DSE/DSE260-Capstone-Project/capstone/venv3.9/lib/python3.9/site-packages/urllib3/connectionpool.py:981: InsecureRequestWarning: Unverified HTTPS request is being made to host 'ucsdonline.maps.arcgis.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
  warnings.warn(


'1.8.1'

### What information is available for your country of interest?

In [ ]:
countries = get_countries()
print("Number of countries for which GeoEnrichment data is available: " + str(len(countries)))

#print a few countries for a sample
countries[0:10]

In [ ]:
# What is available for the US?

usa = Country.get('US')
usa.properties.datasets

### Geoenrichment integrates data from many databases:

* ACS: American Community Survey (https://www.census.gov/programs-surveys/acs, https://doc.arcgis.com/en/esri-demographics/data/acs.htm, http://suave2.sdsc.edu/gallery/sdhhsa)
* ASR: Age, Sex, Race (https://www.census.gov/newsroom/press-kits/2020/population-estimates-detailed.html)
* CRM: Crimes (https://doc.arcgis.com/en/esri-demographics/data/crime-indexes.htm)
* RMP: Retail MarketPlace (https://downloads.esri.com/esri_content_doc/dbl/us/Var_List_Retail-MarketPlace_Summer2020.pdf, https://doc.arcgis.com/en/esri-demographics/data/market-potential.htm)
* Safegraph: 5 million point locations for any transactions (https://www.esri.com/arcgis-blog/products/bus-analyst/data-management/why-and-when-to-use-safegraph-data-in-your-analysis/, https://doc.arcgis.com/en/esri-demographics/data/business.htm)
* Traffic Counts (https://doc.arcgis.com/en/esri-demographics/data/traffic-counts.htm)

Global coverage of geoenrichment: https://doc.arcgis.com/en/arcgis-online/reference/geoenrichment-coverage.htm

Standard geography levels: https://geoenrichdev.arcgis.com/arcgis/rest/services/World/GeoenrichmentServer/Geoenrichment/StandardGeographyLevels

You can also also find variables for geoenrichment with the ESRI Demographics Data Browser at https://doc.arcgis.com/en/esri-demographics/data/data-browser.htm (may be easier!)

In [ ]:
# Listing  specific data collections

df = usa.data_collections
print(df.index.unique().values)

In [ ]:
# A data collection is a preassembled list of attributes that will be used to enrich the input features. 
# Collection attributes can describe various types of information, 
# such as demographic characteristics and geographic context of the locations or areas submitted as input features.

df = usa.data_collections
print(df.shape) # total number of collections
df[2000:2050]     # returns a pandas DF with specific measured variables


In [ ]:
# GeoEnrichment also enables you to create many types of high quality reports 
# for a variety of use cases describing the input area.

# print a sample of the reports available for USA
usa.reports.head(50)

In [ ]:
# Discover named geographies and level of detail

sandiego_in_usa = usa.search('San Diego')
print("number of San Diego's in the US: " + str(len(sandiego_in_usa)))

# list a few of them
sandiego_in_usa[:10]

In [ ]:
# let's put them on a map
usamap = gis.map('United States', zoomlevel=4)
usamap

In [ ]:
for sd in sandiego_in_usa:
    usamap.draw(sd.geometry)

### Working with study areas

GeoEnrichment uses the concept of a study area to define the location of the point or area that you want to enrich with additional information, or create reports about.

#### Accepted forms of study areas

- **Street address locations** - Locations can be passed as strings of input street addresses, points of interest or place names.
    + **Example:** `"380 New York St, Redlands, CA"`

- **Multiple field input addresses** - Locations described as multiple field input addresses, using dictionaries.
    + **Example:** 
        {"Address" : "380 New York Street",
        "City" : "Redlands",
        "Region" : "CA",
        "Postal" : 92373}    
 
- **Point and line geometries** - Point and line locations, using `arcgis.geometry` instances.
    + **Example Point Location: ** 
    
    `arcgis.geometry.Geometry({"x":-122.435,"y":37.785})`

- **Buffered study areas** - `BufferStudyArea` instances to change the ring buffer size or create drive-time service areas around points specified using one of the above methods. BufferStudyArea allows you to buffer point and street address study areas. They can be created using the following parameters:
        * area: the point geometry or street address (string) study area to be buffered
        * radii: list of distances by which to buffer the study area, eg. [1, 2, 3]
        * units: distance unit, eg. Miles, Kilometers, Minutes (when using drive times/travel_mode)
        * overlap: boolean, uses overlapping rings/network service areas when True, or non-overlapping disks when False
        * travel_mode: None or string, one of the supported travel modes when using network service areas
    + **Example Buffered Location: ** 
    
    `pt = arcgis.geometry.Geometry({"x":-122.435,"y":37.785})
    buffered_area = BufferStudyArea(area=pt, radii=[1,2,3], units="Miles", overlap=False)` 

- **Network service areas** - `BufferStudyArea` also allows you to define drive time service areas around points as well as other advanced service areas such as walking and trucking.
    + **Example: **
    
    `pt = arcgis.geometry.Geometry({"x":-122.435,"y":37.785})
    buffered_area = BufferStudyArea(area=pt, radii=[1,2,3], units="Minutes", travel_mode="Driving")` 

- **Named statistical areas** - In all previous examples of different study area types, locations were defined as either points or polygons. Study area locations can also be passed as one or many named statistical areas. This form of study area lets you define an area as a standard geographic statistical feature, such as a census or postal area, for example, to obtain enrichment information for a U.S. state, county, or ZIP Code or a Canadian province or postal code. When the NamedArea instances should be combined together (union), a list of such NamedArea instances should constitute a study area in the list of requested study areas.
    + **Example:** 
    
    `usa.subgeographies.states['California'].zip5['92373']`
   
- **Polygon geometries** - Locations can be given as polygon geometries.
    + **Example Polygon geometry: ** 
    
    `arcgis.geometry.Geometry({"rings":[[[-117.185412,34.063170],[-122.81,37.81],[-117.200570,34.057196],[-117.185412,34.063170]]],"spatialReference":{"wkid":4326}})`


### Creating Reports
The `create_report` method allows you to create many types of high quality reports for a variety of use cases describing the input area. If a point is used as a study area, the service will create a `1` mile ring buffer around the point to collect and append enrichment data. Optionally, you can create a buffer ring or drive time service area around points of interest to generate PDF or Excel reports containing relevant information for the area on demographics, consumer spending, tapestry market, etc.



In [ ]:
# for zip code 92093
report = create_report(study_areas=["92093"],
                     report="tapestry_profileNEW",
                     export_format="PDF", 
                     out_folder=r"../../scratch", out_name="esri_tapestry_profile.pdf")
report

In [ ]:
# check if the item is already published
search_result = gis.content.search(query="esri_tapestry_profile.pdf", max_items=100)
search_result

In [ ]:
# and delete, if found.
gis.content.search(query="esri_tapestry_profile.pdf", max_items=100)[23].delete()

In [ ]:
# You can add this to AGOL!
report_path = "../../scratch/esri_tapestry_profile.pdf"

# Need to give it a unique title, and some parameters. 

report_properties = {'title':'92093 Tapestry Profile PDF', 'type':'PDF', 'tags':'92093, tapestry'}
report_item = gis.content.add(item_properties = report_properties, data=report_path)


In [ ]:
# Let's create a report as Excel file. This is one of the ways to construct features for your ML tasks

# for zip code 92037
report = create_report(study_areas=["92037"],
                     report="tapestry_profileNEW",
                     export_format="XLSX", 
                     out_folder=r"../../scratch", out_name="esri_tapestry_profile_92037.xlsx")
report

In [ ]:
# before adding to AGOL, make sure it's not already published
# check if the item is already published
search_result = gis.content.search(query="esri_tapestry_profile_92037.xlsx", max_items=100)
search_result

In [ ]:
gis.content.search(query="esri_tapestry_profile_92037.xlsx", max_items=100)[0].delete()

In [ ]:
report_path = "/datasets/dsc170sp19-public/esri_tapestry_profile_92037.xlsx"

# Need to give it a unique title, and some parameters. 

report_properties = {'title':'92037 Tapestry Profile XLSX', 'type':'Microsoft Excel', 'tags':'92037, tapestry'}
report_item = gis.content.add(item_properties = report_properties, data=report_path)

# note that format names may be inconsistent across operations. 
# See https://developers.arcgis.com/rest/users-groups-and-items/items-and-item-types.htm
# for types of items in AGOL


**Try it yourself!**

### Geoenrichment: adding features to a named study area

In [ ]:
# Enrich a 1-mile buffer around a street address:

enrich(study_areas=["380 New York St Redlands CA 92373"], data_collections=['Age'])


In [ ]:
# let's try it for a 1-mile buffer around a POI (Scripps Medical Center):
enrich(study_areas=["Scripps Medical Center"], data_collections=['Age'])


In [ ]:
# or for a named study area "San Diego, CA:"
# Note that, in this case, too, it creates a 1-mile ring buffer around the center of the study area 


enrich(study_areas=["San Diego, CA"], data_collections=['transportation'])

In [ ]:
# let's figure out what variables we obtained in this way:
df = usa.data_collections
df[df.index.values == "transportation"]

### Example: Constructing study areas and adding features to them

#### As non-overlapping disks of a given radii

Suppose you are trying to explore how close to UCSD students tend to live. You may look at it by exploring poportion of student-age population within different distance buffers from UCSD.

The example below creates non-overlapping disks of radii 1, 3 and 5 Miles respectively from a street address and enriches these using the 'Age' data collection.

In [ ]:
buffered = BufferStudyArea(area='UCSD',
                           radii=[1,3,5], units='Miles', overlap=False)
enrich(study_areas=[buffered], data_collections=['Age'])

#### As drive-time buffers for given drive-times (or walk times)


In [ ]:
# Alternatively, we can use drive time buffers as study areas.
# Create 5, 10, 15, 20 and 25 minute drive times from a location and enrich these using the 'Age' data collection.
buffered = BufferStudyArea(area='700 Prospect Street, La Jolla, CA', 
                           radii=[5, 10, 15, 20, 25], units='Minutes', 
                           travel_mode='Driving time')
buffered

In [ ]:
# We can explore what other travel modes are supported:

usa = Country("USA")
usa.travel_modes

In [ ]:
# let's enrich these buffers, and explore the content 
drive_time_df = enrich(study_areas=[buffered], data_collections=['Age'])
drive_time_df

In [ ]:
# now, we'll show it on a map and then create a feature layer in AGOL:

# Step 1: create a Spatially-Enabled DataFrame (SEDF) with the enriched data
drive_time_sedf = drive_time_df.spatial


In [ ]:
# spatial objects here are polygons, let's make sure:

drive_time_sedf.geometry_type

In [ ]:
# Step 2: show these drive-time buffers on a map
map4 = gis.map('700 Prospect Street, La Jolla, CA')
map4.zoom = 11
map4

In [ ]:
# Step 3: now, add the layer of drive time zones (a featureset built from the SEDF), to the map:
map4.draw(drive_time_sedf.to_featureset()) 

In [ ]:
# SEDF has a "GeoAccessor" type
type(drive_time_sedf)

In [ ]:
# Step 4: now we can save it as a feature layer, and publish on AGOL
drivetime_lj_fl= drive_time_sedf.to_featurelayer(title='drive_from_art_museum', gis=gis, tags='sample')

Think of other situations where you may use this approach:
 - when you are locating a retail store: what factors you may be interested in?
 - when you are deciding whether to add staff to a nursing home: what factors are you looking at?
 - when you decide which polling places to relocate or consolidate?

In [ ]:
pd.set_option('display.max_columns', None)
drive_time_df

### Working with named statistical areas: counties, zip codes, etc.

More info at https://developers.arcgis.com/python/guide/part3-where-to-enrich-named-stat-areas/

In [ ]:
# get a single zip code. 
zip92122 = usa.subgeographies.states['California'].zip5['92122']

In [ ]:
zip92122_enriched = enrich(study_areas=[zip92122], data_collections=['Age'] )
zip92122_enriched

In [ ]:
# get all zip codes in San Diego county
sd_zips = usa.subgeographies.states['California'].counties['San_Diego_County'].zip5
sd_zips

In [ ]:
# or, get all tracts:
sd_tracts = usa.subgeographies.states['California'].counties['San_Diego_County'].tracts
sd_tracts

In [ ]:
sd_list=list(sd_tracts.values())


In [ ]:
sd_list

In [ ]:
# https://developers.arcgis.com/python/guide/part1-introduction-to-geoenrichment/ should be up to 2.1.0

# can pass a list (best practice) or can pass a dict as output of subgeographies
# The enrich command can take a dict (output of subgeographies), or a list of of values:
sd_list=list(sd_tracts.values())

# Option 1: using subgeographics
sd_tracts_enriched = enrich(study_areas=sd_tracts, data_collections=['Age'])

# Option 2: using a list of area names
# sd_tracts_enriched = enrich(study_areas=sd_list, data_collections=['Age'])

sd_tracts_enriched

In [ ]:
# let's show the tracts on a map

sd_map = gis.map('San Diego County, CA')
sd_map


In [ ]:
sd_tracts_enriched.spatial.plot(map_widget=sd_map,
               renderer_type='c',  # for class breaks renderer
               method='esriClassifyNaturalBreaks',  # classification algorithm
               class_count=5,  # choose the number of classes
               col='fem75',  # numeric column to classify
               cmap='viridis',  # color map to pick colors from for each class
               alpha=0.7  # specify opacity
               )

In [ ]:
# We can add a legend
sd_map.legend=True

### How accurate are the numbers returned for such constructed polygons?

**ApportionmentConfidence** depends on three factors: 

1. **Reliability of the original census data**, on a 1-5 scale, based on 
    1. Census type: from 1 (Census - de jure - Complete Tabulation), to 5 - Sample Survey -de facto
    1. Census completeness: from 1 (final figure) to 4 (provisional figure with questionable reliability)
        1. consider 2021 ACS estimates as an example
    1. Age of Censis: from 1 (1-2 years) to 5 (9-10 years)
1. **Ratio of the population polygon to the number of people** (1.0 - 5.0 scale) (populationToPolygonSizeRating)
    1. The larger the area of a census tabulation area, the less likely the specific locations where people live can reliably be found. For large areas with relatively low populations, this means the likelihood of correctly locating where those people live is even lower. 
1. **Complexity of settlement footprint relative to NoData and zero population cells** (1.0 to 5.0)
    1. Based on Landsat8 panchromatic imagery (15m resolution). When levels of texture are sufficiently high, the likelihood that it represents human settlement is high. However, because this model is largely completed using raster data, underestimation of the footprint edges occur due to resampling. The amount of area is proportional to the complexity of the (raster) human settlement footprint. Complexity is measured as the sum of distances from a given cell to all NoData cells within 8 kilometers (this figure is then scaled to 1.0 to 5.0).
    
Problem is when study area spans more than one country. Then both populationToPolygonSizeRating and ApportionmentConfidence are NULL.

More about Data Apportionment see https://developers.arcgis.com/rest/geoenrichment/api-reference/data-apportionment.htm




## Organizing spatial data for analysis
1. Feature layers, feature sets, feature collections, and more...
2. What you can do with them


### Feature Layers, Feature Collections, Feature Sets, Feature Services... 

Terminology may be daunting...

The __feature layer__ is the primary concept for working with features in a GIS. Users create, import, export, analyze, edit, and visualize features, i.e. “entities in space” as feature layers.

Feature layers can be added to and visualized using maps. They act as inputs to and outputs from feature analysis tools.

Feature layers are created by publishing feature data to a GIS, and are exposed as a broader resource (Item) in the GIS. 
__Feature layer instances__ can be obtained through the __layers__ attribute on __feature layer collection__ items in the GIS. A __feature layer collection__ is a collection of feature layers and tables, with the associated relationships among the entities. A feature layer collection is backed by a [feature service](http://server.arcgis.com/en/server/latest/publish-services/windows/what-is-a-feature-service-.htm) in a web GIS.

You will work with several feature services in MP3, to retrieve current data from several sources



#### Find a feature layer collection online

In [ ]:
# let's find some feature layer and explore it. 
# Note that "feature layer collection" can be "a group feature layer":
# these may include layers at different levels of resolutions, shown with different symbols, etc.

# Search for freeways:

search_results = gis.content.search('title: USA Freeway System',
                                    'Feature Layer', outside_org=True)

# Access the first item that's returned: this is a 'feature layer collection'
freeways = search_results[0]

freeways


#### Find AGOL ID an URL for a feature layer collection

In [ ]:
# when you open the feature layer collection in AGOL, notice the ID of that layer collection (in address bar)

# this unique ID can be also retrieved through Python:
print(freeways.id)

# also, feature layers can be accessed via service URLs

print(freeways.url)


#### Retrieve a layer collection from AGOL by ID

In [ ]:
# here is how you can retrieve the layer collection by ID:

my_new_freeways = gis.content.get('91c6a5f6410b4991ab0db1d7c26daacb')
my_new_freeways

# When you submit MP3, MP4, and final projects, 
# referencing feature layer collections/services with gis.content.get will be the safest option
# They must be shared so that instructors can access them.

#### Use the "layers" property to access individual layers in a collection

In [ ]:
# this is a "feature layer collection" - so we can discover individual layers via the layers property:
freeways.layers 


In [ ]:
# There are two layers here! Why?
#
#
#
#   YOUR THOUGHTS?
#

for lyr in freeways.layers:
    print(lyr.properties.name)

In [ ]:
# each layer has properties, including name, e.g:

for lyr in freeways.layers:
    print(lyr.properties.name + " :::  " + lyr.properties.description)

In [ ]:
# and here are the fields in the first layer:
for f in freeways.layers[0].properties.fields:
    print(f['name'])


In [ ]:
# you can also see how the layer will be rendered (layer properties include rendering information):
print(freeways.layers[0].properties.drawingInfo.renderer) 

#### Feature services

In [ ]:
# Now, let's look at an example of a __feature service__

# Feature Service: serves a collection of feature layers and tables, 
# with the associated relationships among the entities. 
# following the example with freeways: 

from arcgis.features import FeatureLayerCollection

serviceURL = freeways.url
# or:
serviceURL = 'https://services.arcgis.com/P3ePLMYs2RVChkJx/arcgis/rest/services/USA_Freeway_System/FeatureServer'

flc_from_url= FeatureLayerCollection(serviceURL, gis=gis)
flc_from_url.layers


In [ ]:
# Let's try another service:

from arcgis.features import FeatureLayerCollection
fs_url= 'https://services1.arcgis.com/eGSDp8lpKe5izqVc/arcgis/rest/services/Brewery_Locations_in_San_Diego_WFL1/FeatureServer'
breweries = FeatureLayerCollection(fs_url)

In [ ]:
breweries.layers # shows layers in the service

In [ ]:
breweries.tables # shows tables in the service

In [ ]:
# we can also look at properties of each layer or table
breweries.layers[0].properties

In [ ]:
# it can also show what operations are possible over this layer:

print(breweries.layers[0].properties.capabilities) 

# or how it is to be rendered:

print(breweries.layers[0].properties.drawingInfo.renderer.type) 


In [ ]:
# we can explore the same from AGOL UI:
comm_points = gis.content.get('e435c0dd31c3447db9503272edf7abf0')
comm_points

#### Properties of layers. From layers to featuresets, to determine CRS

In [ ]:
# How can we determine CRS of a layer (called "spatial_reference"). 

# By converting it to a featureset - using query() without parameters -  and then retrieving its spatial reference
# note that "spatial reference" is a property of a featureset, but not of a layer

query_result1 = breweries.layers[0].query()
type(query_result1)

In [ ]:
query_result1.spatial_reference

# see more about spatial reference at https://developers.arcgis.com/web-map-specification/objects/spatialReference/
# latestWkid:: the current Well-Known ID
# wkid:: wkid originally assigned to geometry objects


In [ ]:
# change spatial reference:
breweries_fs_4326 = breweries.layers[1].query(out_sr=4326)
breweries_fs_4326.spatial_reference

In [ ]:
# now you get breweries as SEDF in 4326:

breweries_sedf_4326 = breweries_fs_4326.sdf
breweries_sedf_4326

#### Selecting records in a layer

In [ ]:
# featurelayer.query() can be used to filter records, e g.

sedf1 = breweries.layers[1].query(where="TYPE='Brewery'").sdf
sedf1

# query() can be used to execute arbitrary SQL statements (including distance-based queries)

# notice that featureset.sdf will generate a SEDF

#### Another way to create a SEDF from a feature layer

In [ ]:
# alternatively, it can be converted to a spatially-enabled dataframe directly from feature layer

sedf1 = pd.DataFrame.spatial.from_layer(breweries.layers[1])
sedf1


In [ ]:
# Convert back from a SEDF into a feature layer, and publishing on AGOL

my_new_featurelayer = sedf1.spatial.to_featurelayer(title="my sample fl", gis=gis, tags='sample')

### Mapping feature layers and SEDFs


In [ ]:
# Mapping a feature layer
m = gis.map("USA",4)
m.add_layer(freeways)
m



In [ ]:
# mapping a SEDF
fw_sdf = pd.DataFrame.spatial.from_layer(freeways.layers[0])
m1= gis.map("USA", 4)
m1


In [ ]:
# here is the simplest way to add a SEDF to a map
fw_sdf.spatial.plot(map_widget=m1)

# In an earlier version of ArcGIS Python API, only a limited number of vector features
# could be drawn in a map widget! Now it appears fixed, but better use feature layers 
# and not SEDF when you have many features.


In [ ]:
# what would happen if you don't add .spatial to the dataframe?

%matplotlib inline
fw_sdf.plot()   # not too useful

In [ ]:
# yet another way to draw, using a specified symbol. Let's find Hyway 101 by clicking it on the map. 
# Note the ID of this feature

hw101_geom = fw_sdf.iloc[674]['SHAPE']
sym_poly = {
  "type": "esriSFS",
  "style": "esriSFSSolid",
  "color": [0,0,0,0],  # hollow, no fill
    "outline": {
     "type": "esriSLS",
     "style": "esriSLSSolid",
     "color": [0,0,255,255],  # blue line
     "width": 3}
}

m1.draw(shape = hw101_geom, symbol = sym_poly)

# Note that the ID is '675' but we use 'iloc[674]' !!
